In [3]:
import pandas as pd
import os

# Definir caminho da pasta
base_path = r"C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados"

# Caminhos dos arquivos
path_stock = os.path.join(base_path, "stock.xlsx")
path_etf = os.path.join(base_path, "etf.xlsx")
path_index = os.path.join(base_path, "Index.xlsx")
path_mutual = os.path.join(base_path, "Mutual Fund.xlsx")

# Carregar arquivos
df_stock = pd.read_excel(path_stock)
df_etf = pd.read_excel(path_etf)
df_index = pd.read_excel(path_index)
df_mutual = pd.read_excel(path_mutual)

# Exibir tamanhos e primeiras linhas
print(f"Stocks: {df_stock.shape}")
print(f"ETFs: {df_etf.shape}")
print(f"Índices: {df_index.shape}")
print(f"Mutual Funds: {df_mutual.shape}")

df_stock.head()


Stocks: (106328, 5)
ETFs: (21192, 3)
Índices: (80013, 3)
Mutual Funds: (24922, 3)


Ticker                                     Name Exchange  \
0   OEDV  Osage Exploration and Development, Inc.      PNK   
1   AAPL                               Apple Inc.      NMS   
2    BAC              Bank of America Corporation      NYQ   
3   AMZN                         Amazon.com, Inc.      NMS   
4      T                                AT&T Inc.      NYQ   

                 Category Name Country  
0                          NaN     USA  
1         Electronic Equipment     USA  
2           Money Center Banks     USA  
3  Catalog & Mail Order Houses     USA  
4  Telecom Services - Domestic     USA

In [4]:
# Selecionar apenas a coluna 'Ticker'
tickers_stock = df_stock['Ticker'].dropna().unique().tolist()
tickers_etf = df_etf['Ticker'].dropna().unique().tolist()
tickers_index = df_index['Ticker'].dropna().unique().tolist()
tickers_mutual = df_mutual['Ticker'].dropna().unique().tolist()

print(f"Primeiros 5 Stocks: {tickers_stock[:5]}")
print(f"Total Stocks: {len(tickers_stock)}")


Primeiros 5 Stocks: ['OEDV', 'AAPL', 'BAC', 'AMZN', 'T']
Total Stocks: 106328


In [23]:
import yfinance as yf
import time


# Função para testar uma lista de tickers e separar válidos/falhos
def testar_tickers(lista_tickers, nome_categoria, espera=1):
    validos = []
    falhos = []

    print(f"\n🔍 Verificando {nome_categoria}...\n")

    for ticker in lista_tickers:
        try:
            ativo = yf.Ticker(ticker)
            hist = ativo.history(start="2000-01-01", end="2025-07-01")

            if hist.empty or len(hist) < 20:
                print(f"⚠️ {ticker} — poucos dados ou vazio")
                falhos.append(ticker)
            else:
                print(f"✅ {ticker} — OK ({len(hist)} registros)")
                validos.append(ticker)

            time.sleep(espera)
        except Exception as e:
            print(f"❌ {ticker} — erro: {e}")
            falhos.append(ticker)

    print(f"\n📦 Resultado — {nome_categoria}:")
    print(f"✅ Válidos: {len(validos)}")
    print(f"❌ Falhos: {len(falhos)}\n")

    return validos, falhos



In [25]:
import re

def limpar_tickers(tickers, tipo):
    tickers = pd.Series(tickers).dropna().astype(str).str.strip().str.upper().unique()

    if tipo == "STOCK":
        # Ex: AAPL, MSFT, AMZN — letras puras, no máximo 5
        filtrado = [t for t in tickers if re.fullmatch(r"[A-Z]{1,5}", t)]

    elif tipo == "ETF":
        # Ex: SPY, QQQ — letras/números, até 5-6 chars
        filtrado = [t for t in tickers if re.fullmatch(r"[A-Z0-9]{2,6}", t)]

    elif tipo == "INDEX":
        # Ex: ^GSPC, ^NDX — começa com ^
        filtrado = [t for t in tickers if t.startswith("^") and len(t) <= 7]

    elif tipo == "MUTUAL":
        # Ex: HDFCBANK.BO — conter "." e até 10 chars
        filtrado = [t for t in tickers if "." in t and len(t) <= 10]

    else:
        filtrado = []

    print(f"🎯 {tipo}: {len(filtrado)} tickers limpos de {len(tickers)}")
    return filtrado




In [26]:
tickers_stock_limpos = limpar_tickers(tickers_stock, "STOCK")
tickers_etf_limpos = limpar_tickers(tickers_etf, "ETF")
tickers_index_limpos = limpar_tickers(tickers_index, "INDEX")
tickers_mutual_limpos = limpar_tickers(tickers_mutual, "MUTUAL")


🎯 STOCK: 21169 tickers limpos de 106328
🎯 ETF: 2060 tickers limpos de 21192
🎯 INDEX: 5456 tickers limpos de 80013
🎯 MUTUAL: 8219 tickers limpos de 24922


In [32]:
validos_stock, falhos_stock = testar_tickers(tickers_stock_limpos, "STOCK", espera=1)
validos_etf, falhos_etf = testar_tickers(tickers_etf_limpos, "ETF", espera=1)
validos_index, falhos_index = testar_tickers(tickers_index_limpos, "INDEX", espera=1)
validos_mutual, falhos_mutual = testar_tickers(tickers_mutual_limpos, "MUTUAL FUND", espera=1)



$OEDV: possibly delisted; no price data found  (1d 2000-01-01 -> 2025-07-01)



🔍 Verificando STOCK...

⚠️ OEDV — poucos dados ou vazio
✅ AAPL — OK (6411 registros)
✅ BAC — OK (6411 registros)
✅ AMZN — OK (6411 registros)
✅ T — OK (6411 registros)
✅ GOOG — OK (5249 registros)
✅ MO — OK (6411 registros)
✅ DAL — OK (4569 registros)
✅ AA — OK (6411 registros)
✅ AXP — OK (6411 registros)
✅ DD — OK (6411 registros)
✅ BABA — OK (2710 registros)
✅ ABT — OK (6411 registros)
✅ UA — OK (2331 registros)
✅ AMAT — OK (6411 registros)
✅ AMGN — OK (6411 registros)
✅ AAL — OK (4970 registros)
✅ AIG — OK (6411 registros)
✅ ALL — OK (6411 registros)
✅ ADBE — OK (6411 registros)
✅ GOOGL — OK (5249 registros)
✅ ACN — OK (6022 registros)
✅ ABBV — OK (3142 registros)
✅ MT — OK (6411 registros)
✅ LLY — OK (6411 registros)


$AGN: possibly delisted; no timezone found


⚠️ AGN — poucos dados ou vazio
✅ APA — OK (6411 registros)
✅ ADP — OK (6411 registros)


$APC: possibly delisted; no timezone found


...

⚠️ UIVC.SG — poucos dados ou vazio


$XP63.BE: possibly delisted; no price data found  (1d 2000-01-01 -> 2025-07-01)


⚠️ XP63.BE — poucos dados ou vazio


$XEY7.SG: possibly delisted; no price data found  (1d 2000-01-01 -> 2025-07-01)


⚠️ XEY7.SG — poucos dados ou vazio

📦 Resultado — MUTUAL FUND:
✅ Válidos: 702
❌ Falhos: 7517



In [33]:
import pandas as pd
import os

# Caminho de saída
base_path = r"C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados"

# Função auxiliar para salvar listas
def salvar_em_excel(lista, nome, tipo):
    df = pd.DataFrame(lista, columns=["Ticker"])
    path = os.path.join(base_path, f"{tipo.lower()}_{nome}.xlsx")
    df.to_excel(path, index=False)
    print(f"💾 {tipo.upper()} — {nome} salvo em: {path}")

# Salvar todos
salvar_em_excel(validos_stock, "validos", "stock")
salvar_em_excel(falhos_stock, "falhos", "stock")

salvar_em_excel(validos_etf, "validos", "etf")
salvar_em_excel(falhos_etf, "falhos", "etf")

salvar_em_excel(validos_index, "validos", "index")
salvar_em_excel(falhos_index, "falhos", "index")

salvar_em_excel(validos_mutual, "validos", "mutual")
salvar_em_excel(falhos_mutual, "falhos", "mutual")


💾 STOCK — validos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\stock_validos.xlsx
💾 STOCK — falhos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\stock_falhos.xlsx
💾 ETF — validos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\etf_validos.xlsx
💾 ETF — falhos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\etf_falhos.xlsx
💾 INDEX — validos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\index_validos.xlsx
💾 INDEX — falhos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\index_falhos.xlsx
💾 MUTUAL — validos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\mutual_validos.xlsx
💾 MUTUAL — falhos salvo em: C:\Users\mathe\OneDrive\Área de Trabalho\MASTER\FLI\FMI\dados\mutual_falhos.xlsx


In [1]:
import yfinance as yf
import pandas as pd
from tqdm import tqdm
import time
import os

# Caminho base onde os dados estão e serão salvos
caminho_base = "C:/Users/mathe/OneDrive/Área de Trabalho/MASTER/FLI/FMI/dados/"

# Colunas desejadas do dicionário `info`
colunas_desejadas = {
    "symbol": "Ticker",
    "shortName": "Nome Curto",
    "quoteType": "Tipo de Ativo",
    "sector": "Setor",
    "industry": "Indústria",
    "currency": "Moeda",
    "currencySymbol": "Símbolo da Moeda",
    "country": "País",
    "exchange": "Bolsa de Valores",
    "maxAge": "Idade Máxima dos Dados",
    "fullTimeEmployees": "Funcionários Tempo Integral",
    "auditRisk": "Risco Auditoria",
    "boardRisk": "Risco Diretoria",
    "compensationRisk": "Risco Compensação",
    "shareHolderRightsRisk": "Risco Direitos Acionistas",
    "overallRisk": "Risco Geral",
    "governanceEpochDate": "Data Governança",
    "website": "Website"
}

# Colunas ESG
colunas_esg = {
    "totalEsg": "Pontuação ESG Total",
    "environmentScore": "Pontuação Ambiental",
    "socialScore": "Pontuação Social",
    "governanceScore": "Pontuação Governança"
}

def extrair_dados_dos_ativos_ativos(caminho_entrada, nome_categoria, espera=1):
    print(f"\n🔍 Lendo e filtrando: {caminho_entrada}")
    
    df = pd.read_excel(caminho_entrada)
    tickers = df.iloc[:, 0].dropna().unique().tolist()

    dados_finais = []

    for ticker in tqdm(tickers, desc=f"📥 Coletando dados - {nome_categoria.upper()}"):
        try:
            ativo = yf.Ticker(ticker)
            info = ativo.info
            if info.get("regularMarketPrice", 0) in [None, 0]:
                continue  # pula se não está ativo

            esg = info.get("esgScores", {}) or {}

            registro = {novo_nome: info.get(origem, None) for origem, novo_nome in colunas_desejadas.items()}
            registro.update({novo_nome: esg.get(origem, None) for origem, novo_nome in colunas_esg.items()})
            registro["Categoria Original"] = nome_categoria.upper()

            dados_finais.append(registro)
        except:
            continue
        time.sleep(espera)

    # Salvar resultado com nome *_ativos.xlsx
    output_path = os.path.join(caminho_base, f"{nome_categoria}_ativos.xlsx")
    pd.DataFrame(dados_finais).to_excel(output_path, index=False)
    print(f"✅ {nome_categoria.upper()} — {len(dados_finais)} ativos salvos em {output_path}\n")

# Dicionário com os caminhos dos arquivos válidos
caminhos_validos = {
    "stock": os.path.join(caminho_base, "stock_validos.xlsx"),
    "etf": os.path.join(caminho_base, "etf_validos.xlsx"),
    "index": os.path.join(caminho_base, "index_validos.xlsx"),
    "mutual": os.path.join(caminho_base, "mutual_validos.xlsx")
}

# Executar para cada categoria
for nome, caminho in caminhos_validos.items():
    extrair_dados_dos_ativos_ativos(caminho, nome, espera=1)



KeyboardInterrupt: 